## Using Lets-Plot with GeoTools to Create Maps


The Let's-Plot library allows to easily visualize geospatial features from GeoTools `SimpleFeatureCollection`.

`SimpleFeatureCollection` is a collection of `SimpleFeature`-s. Each `SimpleFeature` have a "geometry" attribute as well as optional "data" attributes.

The Let's-Plot library understands the following three geometry types:

- Points / Multi-Points
- Lines / Multi-Lines
- Polygons / Multi-Polygons

These shapes can be plotted using various geometry layers, depending on the type of the shape:

- `geomPoint`, `geomText` with Points / Multi-Points
- `geomPath` with Lines / Multi-Lines
- `geomPolygon`, `geomMap` with Polygons / Multi-Polygons
- `geomRect` when used with Polygon shapes will display corresponding bounding boxes

Apart from `SimpleFeatureCollection` the Lets-Plot library can also plot an individual `Geometry` (org.locationtech.jts.geom) and a `ReferencedEnvelope` (org.geotools.geometry.jts).

Before passing to a Lets-Plot geometry layer (via `map` or `data` parameters) any 'foreign' object must be converted to a Lets-Plot `SpatialDataset` object. This is done by the `toSpatialDataset()` extension method provided by Lets-Plot GeoTools extension (see the `%use lets-plot-gt` 'magic').


Shapfiles used in this tutorial:
- naturalearth_lowres.shp
- naturalearth_cities.shp 

all are the copies of shapefiles distributed with the [GeoPandas](https://geopandas.org/) Python package.

In [1]:
%useLatestDescriptors
%use lets-plot

In [2]:
// Initialize Lets-Plot GeoTools extension. 
%use lets-plot-gt

In [3]:
LetsPlot.getInfo()

Lets-Plot Kotlin API v.4.9.3. Frontend: Notebook with dynamically loaded JS. Lets-Plot JS v.4.5.2.

In [4]:
@file:DependsOn("org.geotools:gt-shapefile:[30,)")
@file:DependsOn("org.geotools:gt-cql:[30,)")

In [5]:
import org.geotools.data.shapefile.ShapefileDataStoreFactory
import org.geotools.data.simple.SimpleFeatureCollection
import java.net.URL

val factory = ShapefileDataStoreFactory()

### Polygon shapes - Naturalearth low-resolution world dataset.

In [6]:
val worldFeatures : SimpleFeatureCollection = with("naturalearth_lowres") {
    val url = "https://raw.githubusercontent.com/JetBrains/lets-plot-kotlin/master/docs/examples/shp/${this}/${this}.shp"
    factory.createDataStore(URL(url)).featureSource.features
}

// Convert Feature Collection to SpatialDataset.
// Use 10 decimals to encode floating point numbers (this is the default).
val world = worldFeatures.toSpatialDataset(10)

In [7]:
world["continent"]?.distinct()

[Oceania, Africa, North America, Asia, South America, Europe, Seven seas (open ocean), Antarctica]

#### geomPolygon()

In [8]:
val voidTheme = theme(axis="blank", panelGrid="blank")

// Use the parameter `map` in `geomPolygon()` to display Polygons / Multi-Polygons 
letsPlot() + 
    geomPolygon(map = world, fill = "white", color = "gray") + 
    ggsize(700, 400) + 
    voidTheme

#### geomMap()

*geomMap()* is very similar to *geomPolygon()* but it automatically applies the `Mercator` projection and other defaults that are more suitable for displaying blank maps. 

In [9]:
letsPlot() + 
    geomMap(map = world) + 
    ggsize(700, 400) + 
    voidTheme

In [10]:
// When applying Mercator projection to the world map, Antarctica becomes disproportionally large so 
// in the future let's show only part of it above 85-th parallel south:
val worldLimits = coordMap(ylim = -70 to 85)

### Point shapes - Naturalearth world capitals dataset.

In [11]:
val cityFeatures : SimpleFeatureCollection = with("naturalearth_cities") {
    val url = "https://raw.githubusercontent.com/JetBrains/lets-plot-kotlin/master/docs/examples/shp/${this}/${this}.shp"
    factory.createDataStore(URL(url)).featureSource.features
}

#### geomPoint()

In [12]:
// Use parameter `map` in `geomPoint()` to display Point shapes
val cities = cityFeatures.toSpatialDataset(10)
letsPlot() + 
    geomMap(map = world) + 
    geomPoint(map = cities, color = "red") +
    ggsize(800, 600) + voidTheme + worldLimits

### geomText()

The situation with *geomText()* is different because in order to display labels we have to specify mapping for the aesthetic "label".

Aesthetic mapping binds a variable in *data* (passed via `data` parameter) with its representation on the screen.

Variables in a SpatialDataset passed via the `map` parameter can not be used in the aesthetic mapping.

Fortunately, such a SpatialDataset can as well be passed via the `data` parameter and Lets-Plot will undersand that its *geometries* should be mapped to the "x" and "y" aesthetic automatically.

In the next example we are going to show names of cities as labels on map. 

Let's only show South American capitals because too many labels on the entire world map would quickly become not legible.

In [13]:
import org.geotools.filter.text.cql2.CQL

In [14]:
// Obtain bounding box of South America and use it to set the limits.
val southAm = worldFeatures.subCollection(
    CQL.toFilter("continent = 'South America'")
)
val southAmBounds = southAm.bounds

// Let's use slightly expanded boundind box.
southAmBounds.expandBy(4.0)

// Define limits to use later with city markers and labels. 
val southAmLimits = coordMap(
    xlim = southAmBounds.minX to southAmBounds.maxX,
    ylim = southAmBounds.minY to southAmBounds.maxY
)


letsPlot() + 
    geomMap(map = southAm.toSpatialDataset()) +
    geomRect(map = southAmBounds.toSpatialDataset(), alpha = 0, color = "#EFC623")

<path d="M64.38060863839561 273.222627271423 L64.38060863839561 273.222627271423 L67.29758754659116 279.9152037410945 L71.58721278197936 283.295753931885 L76.2068091893205 284.7189403031434 L74.72193891553226 287.5918430497584 L71.58721278197936 287.8811112238817 L69.90462378195693 285.8455118380631 L64.38278719914487 285.688856827221 L64.38060863839561 273.222627271423 ZM100.70672842761138 172.89591636987615 L100.70672842761138 172.89591636987615 L98.9997647032753 179.94387750571775 L99.03207773710574 183.84284134260548 L98.31616073014592 184.72025239334516 L97.83496082707407 189.36211711300268 L102.02431583071623 192.80659272399802 L101.57380904686926 195.60533494624448 L103.63570459233242 197.38698664881755 L103.46808605781439 199.39608575601503 L100.29748683739629 204.73271564187408 L95.40500362641637 206.9926424015628 L88.78714081916945 207.8744803798034 L85.16236869263639 207.44757553549644 L85.85594792923337 209.98438868686645 L85.1802730122393 213.19902943940752 L85.78919039496873 215.38500447761137 L83.80999575432205 216.9199977877875 L80.42880763253709 217.52437512773184 L77.25582116968124 215.93278013319548 L75.98231249603276 217.0755528002187 L76.44253876784327 221.45776751071304 L78.67034767460748 222.79874223788636 L80.47680826075543 221.39415798559276 L81.45975540510372 223.71173048407056 L78.42156289093731 225.1059112812297 L75.77189411188866 227.91994289952808 L75.28677231005483 232.5345798351548 L74.50657026987946 235.02313082884783 L71.38934297382448 235.03640281721928 L68.8029361236652 237.43936245230864 L67.85673546357745 240.99674646406078 L71.10193601545413 244.517366022684 L74.25659186532039 245.49820103855154 L73.12128748712519 249.89572225697384 L69.22402866844752 252.69992509816538 L67.07951747677919 258.6304892980445 L64.06801092479438 260.658726836082 L62.71580850403265 263.0879744292368 L63.78154181180881 268.56370338740646 L65.9777197539633 271.6705374644338 L61.52849634024594 270.553744100845 L53.55493550686211 269.8357373477172 L52.18687497415988 266.7302294771422 L52.25098949015273 262.79880524385663 L50.054129478447464 263.13458585372257 L48.89162758640259 261.25081701339536 L48.603282782647454 255.82435278798764 L51.13478305277931 253.60783755474813 L52.181077384958286 250.44486374342753 L51.79766917015138 247.95144502375123 L53.54683593383413 243.7965880891287 L54.75205241689375 237.48100503266716 L54.39797318287009 234.72866225686687 L55.838418321485875 233.84647438705315 L55.48527693284697 232.1007660093764 L53.95479864388898 231.17693463148544 L55.042272911418564 229.25242246333445 L53.552889298869786 227.52533066904996 L52.78249200526926 222.33414510394556 L54.10928734433955 221.4283721578182 L53.55186619487361 216.06211093560063 L55.20903885949309 207.82187860057783 L57.18507892953994 206.28622940142233 L56.18209599865517 202.1948958412218 L56.171353407025464 198.3931312282351 L58.66960279794202 195.71829566275215 L58.592784741268446 192.32855797599314 L60.47606338408988 188.41164906777286 L60.4844187332819 184.7624682996961 L59.62773967087833 184.0422426309179 L58.107662939434675 177.3084270631365 L60.140485279948564 173.35458940511478 L59.82852382633024 169.6701546654219 L61.007906933981815 166.2443625510532 L63.16887304787002 162.7394415476685 L65.49745769594631 160.43207437248827 L64.50999184222667 158.98256754546892 L65.19896711117084 157.79730013619402 L65.09452524693094 151.71215183450425 L68.68860425456901 149.92673450050944 L69.82109509660984 146.188192894474 L69.42037937280944 145.29142297158643 L72.17014182460926 142.0690525101264 L76.4876406012958 142.9355355899342 L78.42744573908024 145.51388847899045 L79.71493683356962 142.64286477750022 L83.47782799694454 142.79000673052002 L90.07693389781514 149.40466560673397 L92.77477382263484 149.95380551095042 L96.80648555555655 152.63029977562735 L100.20489592772356 154.05304989490764 L100.6785930683769 155.66487457682732 L97.42998217006635 161.2631153086257 L100.75745733304277 162.2734392174858 L104.4632251911753 162.8409754708768

In [15]:
// Add `text` layer and use the `data` parameter to pass `cities` SpartialDataset.
// Also configure `tooltip` in the points layer to show the city name.
letsPlot() + 
    geomMap(map = southAm.toSpatialDataset(), fill="#e5f5e0") +
    geomPoint(data = cities, color = "red", size = 3, tooltips = layerTooltips().line("@name")) +
    geomText(data = cities, vjust = 1, position = positionNudge(y = -.5)) { label = "name" } +
    geomRect(map = southAmBounds.toSpatialDataset(), alpha = 0, fill = "black", color="#EFC623", size=16) +
    southAmLimits +
    ggsize(450, 691) + 
    voidTheme

<path d="M124.515948719069 584.8062929279486 L124.515948719069 584.8062929279486 L127.36601671014967 590.5066634827009 L131.0769439019764 599.8595255225982 L140.72535460072578 607.4632052938289 L151.11595073784054 610.6642976637365 L147.77611626519644 617.126154836767 L140.72535460072578 617.7767893311268 L136.94080261341327 613.198231108727 L124.52084883217623 612.8458758796146 L124.515948719069 584.8062929279486 ZM206.22222924140516 359.14711346230513 L206.22222924140516 359.14711346230513 L202.38285256943095 374.999692626198 L202.4555324433618 383.7694108028629 L200.84526093237218 385.7429217052416 L199.7629252880521 396.1836046940058 L209.18580384269632 403.9310682865219 L208.17250449027983 410.226120399092 L212.8102091728312 414.2334885035915 L212.43319431185677 418.75244115260483 L205.30174534812 430.7558200168492 L194.297360403989 435.83894507558114 L179.41217701185093 437.8224132148556 L171.25918269485317 436.8622003661482 L172.8192111261497 442.5681102783906 L171.29945386525412 449.7986193619297 L172.6690571913707 454.71540900868223 L168.21736696254004 458.1679823836782 L160.61225232931224 459.52737404910715 L153.47543387658442 455.9474897163979 L150.61100306094744 458.51786344876604 L151.6461639062701 468.37453040142674 L156.65704810041058 471.3907087840217 L160.72021741936896 468.23145710503485 L162.93110467021688 473.4442414538795 L156.09747059964275 476.5800932314028 L150.13772092617234 482.9095349151708 L149.0465639774497 493.28897599390075 L147.29169978802986 498.8863325727111 L140.28029726606377 498.9161845032575 L134.46283906050166 504.3210252946142 L132.33460359213478 512.3224473478493 L139.63384909871365 520.2411772022471 L146.7294375435087 522.4473137623208 L144.175861809538 532.3384087749514 L135.40997863361014 538.645743147943 L130.58645126469588 551.9850247718202 L123.81284041500714 556.547024407631 L120.77140821815192 562.0109932117928 L123.16850169007864 574.3272397285293 L128.1082401498938 581.3152653725265 L118.10085432236428 578.8033254136113 L100.16637626650038 577.1883535551138 L97.08927531806137 570.2033108720566 L97.23348446177567 561.3605813671976 L92.29221186161271 562.1158336447011 L89.677462302609 557.8787792551841 L89.02890469283727 545.6733411071436 L94.72286464270144 540.6878591321912 L97.07623512955774 533.5735615685608 L96.21385678209435 527.9652562898341 L100.14815835636375 518.6199722848185 L102.85898342181008 504.4146895883012 L102.0625730870388 498.2240011184601 L105.30248462330246 496.239745987919 L104.50818373095274 492.3132231651045 L101.0657657370532 490.2353016542113 L103.51175991642526 485.9066056087208 L100.16177384694129 482.0219560108431 L98.4289629177855 470.3457168064609 L101.41324840709308 468.3084131017092 L100.15947263716168 456.2383861535294 L101.9034060804994 446.26838249828626 L103.88685710307823 437.70409901685383 L108.33145193521204 434.250050387984 L106.075499326304 425.0476459054818 L106.05133662436049 416.49655242918925 L111.67050725787203 410.48019653066166 L111.49772476075498 402.85585184594004 L115.73367657683013 394.0457708383205 L115.75246978978294 385.83787554855957 L113.82559017267783 384.217912808965 L110.40656781203245 369.07192345036134 L114.97887978396534 360.17878070071913 L114.277202583389 351.89159065250055 L116.92992210301395 344.1861507890634 L121.79046059501741 336.30273080441106 L127.02801394725321 331.112900710329 L124.80696301975513 327.8526072323934 L126.35663600778554 325.18665248693367 L126.12172084736164 311.49967361214937 L134.20567887319777 307.4838356865107 L136.7529262799036 299.07494613321916 L135.85161913428692 297.05789241791433 L142.03650382773117 289.80999733859716 L151.74760890170387 291.7589285758842 L156.11070255624657 297.5582714636249 L159.00658323788184 291.1006407201983 L167.47024086918788 291.4315987680108 L168.66821230233523 293.1466850265434 L182.3132354158613 306.30957573983 L188.38133371484662 307.5447249746029 L197.44963420349637 313.5648116911324 L205.09348586751935 316.7649228242134 L206.15894597395055 320.3903086

### Choropleth

As we saw earlier, *Lets-Plot* geom-layers accept *SpatialDataset* in their `data` parameter. 

This makes it easy to bind aesthetics with variables in *SpatialDataset*.

In [16]:
// Create choropleth by mapping the `continent` variable to the `fill` aesthetic.
letsPlot() + 
    geomMap(data = world, color = "white") { fill = "continent" } + 
    ggsize(1000, 600) + voidTheme + worldLimits

In [17]:
// Create another choropleth by mapping the `GDP estimate` variable to the `fill` aesthetic.
letsPlot() + 
    geomMap(data = world, color = "white") { fill = "gdp_md_est" } + 
    ggsize(900, 600) + voidTheme + worldLimits + labs(fill = "GDP (mil$)")

### Joining `data` and `geometry` datasets

In this example we will use both: the `data` and the `map` parameters.

We will use the `data` parameter to pass "average temperature per continent" dataset to the geom layer.

The continent geometries *SpatialDataset* is passed via the `map` parameter as before.

For this to work it is also necessary to specify fields by which *Lets-Plot* will join `data` and `map` datasets. We will do that using the *mapJoin* parameter.

In [18]:
// Average temperatures
val climateData = mapOf(
    "region" to listOf("Europe", "Asia", "North America", "Africa", "Australia", "Oceania"),
    "avg_temp" to listOf(8.6, 16.6, 11.7, 21.9, 14.9, 23.9)
)

In [19]:
// Join `data` and `map` using the `mapJoin` parameter.
// For the sake of the demo let's use `geom_rect` and customize the tooltip.
letsPlot() + geomRect(data = climateData,
                        map = world,
                        mapJoin = "region" to "continent",
                        color = "white",
                        tooltips=layerTooltips().line("^fill C\u00b0")) { fill = "avg_temp" } + 
    scaleFillGradient(low = "light_blue", high = "dark_green", name="Average t[C\u00b0]") + 
    ggsize(900, 500) + voidTheme